In [1]:
import torch 
from torch import nn

import ray
from ray.rllib.agents import ppo
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.utils.annotations import override

#from models import VisualEncoder
from train import *
from wrappers_2 import *

/root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [2]:
class VisualEncoder(nn.Module):
    def __init__(self):
        super().__init__()

        self.cnn = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=2, stride=2, padding=0),  
            nn.ELU(),
            nn.Conv2d(32, 32, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(32, 64, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(64, 128, kernel_size=2, stride=2, padding=0),
            nn.ELU(), 
            nn.Conv2d(128, 256, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Conv2d(256, 512, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Flatten(),
        )

    def forward(self, x):
        return self.cnn(x)

In [3]:
class MyModelClass(TorchModelV2, nn.Module):
    def __init__(self, obs_space, action_space, num_outputs, model_config, name):
        TorchModelV2.__init__(self, obs_space, action_space, num_outputs, model_config, name)
        nn.Module.__init__(self)
        features_dim = 512
        self.encoder = VisualEncoder()
        self.encoder.load_state_dict(
            torch.load("/IGLU-Minecraft/models/AngelaCNN/encoder_weigths.pth", map_location=torch.device('cpu'))
        )
        self.bn = nn.BatchNorm1d(features_dim, affine=False)
        self.mlp = nn.Sequential(
            nn.Linear(features_dim, 256),
            nn.ELU(),
            nn.Linear(256, 256),
            nn.ELU(),
            nn.Linear(256, 256),
            nn.ELU(),
            #nn.Linear(256, 256),
            #nn.ELU(),
            #nn.Linear(256, 256),
            #nn.ELU(),
        )
        self.action_head = nn.Linear(256, action_space.n)
        self.value_head = nn.Linear(256, 1)
        self.last_value = None
        
        self.use_cuda = torch.cuda.is_available()
        if self.use_cuda:
            self.encoder.cuda()
            self.mlp.cuda()
            self.action_head.cuda()
            self.value_head.cuda()
        
    @override(TorchModelV2)
    def forward(self, input_dict, state, seq_lens):
        obs = input_dict['obs'].permute(0, 3, 1, 2).float() / 255.0
        if self.use_cuda:
            obs.cuda()
        
        with torch.no_grad():
            features = self.encoder(obs)
        features = self.bn(features)
        features = self.mlp(features)
        action = self.action_head(features)
        self.last_value = self.value_head(features).squeeze(1)
        return action, state
    
    @override(TorchModelV2)
    def value_function(self):
        assert self.last_value is not None, "must call forward() first"
        return self.last_value

In [4]:
ModelCatalog.register_custom_model("my_torch_model", MyModelClass)

In [5]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="0"

class RewardWrapper(gym.RewardWrapper):
    def __init__(self, env):
        super().__init__(env)
    
    def reward(self, rew):
        if rew == 0:
            rew = -0.01
        return rew
    
def env_creator(env_config):
    env = gym.make('IGLUSilentBuilder-v0', max_steps=1000)
    env.update_taskset(TaskSet(preset=['C32']))
    env = PovOnlyWrapper(env)
    env = SelectAndPlace(env)
    env = Discretization(env, flat_action_space('human-level'))
    env = RewardWrapper(env)
    return env

from ray.tune.registry import register_env
register_env("my_env", env_creator)

from ray import tune
from ray.rllib.agents.ppo import PPOTrainer

In [6]:
from ray.tune.integration.wandb import WandbLogger

analysis = tune.run(PPOTrainer, 
         config={
             "env": "my_env", 
             "framework": "torch",
             "num_gpus": 1,
             "num_workers": 1,
             "sgd_minibatch_size": 256,
             "clip_param": 0.2,
             "entropy_coeff": 0.01,
             "lambda": 0.95,
             "train_batch_size": 1000,
             #"gamma": 0.99,
             "model": {
                    # Specify our custom model from above.
                    "custom_model": "my_torch_model",
                    # Extra kwargs to be passed to your model's c'tor.
                    "custom_model_config": {},
              },
             "logger_config": {
                  "wandb": {
                      "project": "IGLU-Minecraft",
                      "name":  "PPO C32 pretrained (frozen AngelaCNN + BN + MLP) (3 noops after placement) r: -0.01"
                  }
              }

        },
        loggers=[WandbLogger])

/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/_private/services.py:238: UserWarning: Not all Ray Dashboard dependencies were found. To use the dashboard please install Ray using `pip install ray[default]`. To disable this message, set RAY_DISABLE_IMPORT_WARNING env var to '1'.
  warnings.warn(warning_message)


2021-10-23 19:59:37,170	INFO wandb.py:170 -- Already logged into W&B.
2021-10-23 19:59:37,180	ERROR syncer.py:72 -- Log sync requires rsync to be installed.
wandb: Currently logged in as: linar (use `wandb login --relogin` to force relogin)
wandb: WARNING Tried to auto resume run with id aa44d_00000 but id bff91_00000 is set.
wandb: wandb version 0.12.5 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
(pid=57533) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=57533)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


(pid=57533) 2021-10-23 19:59:40,655	INFO ppo.py:159 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider setting simple_optimizer=True if this doesn't work for you.
(pid=57533) 2021-10-23 19:59:40,655	INFO trainer.py:728 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
(pid=57527) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=57527)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=57533) 2021-10-23 19:59:46,762	WARNING util.py:55 -- Install gputil for GPU system monitoring.
(pid=57527) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=57527)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=57527) /root/miniconda/envs/py37/lib/python3.7/

Result for PPO_my_env_bff91_00000:
  agent_timesteps_total: 1000
  custom_metrics: {}
  date: 2021-10-23_20-00-51
  done: false
  episode_len_mean: 404.0
  episode_media: {}
  episode_reward_max: -4.089999999999957
  episode_reward_mean: -5.504999999999947
  episode_reward_min: -6.919999999999936
  episodes_this_iter: 2
  episodes_total: 2
  experiment_id: 308d04df514f4288854eb163945dc05a
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.8842074553171795
          entropy_coeff: 0.009999999999999998
          kl: 0.006456960763575302
          policy_loss: -0.11997320271200604
          total_loss: -0.08765164100461537
          vf_explained_var: -0.333754301071167
          vf_loss: 0.05987224327141626
    num_agent_steps_sampled: 1000
    num_agent_steps_trained: 1000
    num_steps_sampled: 1000
    num_steps_trained: 1000
  iterations_sinc

Result for PPO_my_env_bff91_00000:
  agent_timesteps_total: 2000
  custom_metrics: {}
  date: 2021-10-23_20-01-16
  done: false
  episode_len_mean: 397.0
  episode_media: {}
  episode_reward_max: -3.8099999999999627
  episode_reward_mean: -6.624999999999953
  episode_reward_min: -11.679999999999955
  episodes_this_iter: 2
  episodes_total: 4
  experiment_id: 308d04df514f4288854eb163945dc05a
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.8800373209847345
          entropy_coeff: 0.009999999999999998
          kl: 0.005599747898264063
          policy_loss: 0.003479890525341034
          total_loss: 0.2959221008751127
          vf_explained_var: 0.006927939131855965
          vf_loss: 0.32012263719613354
    num_agent_steps_sampled: 2000
    num_agent_steps_trained: 2000
    num_steps_sampled: 2000
    num_steps_trained: 2000
  iterations_si

...

Result for PPO_my_env_bff91_00000:
  agent_timesteps_total: 1362000
  custom_metrics: {}
  date: 2021-10-24_08-00-00
  done: false
  episode_len_mean: 225.62
  episode_media: {}
  episode_reward_max: -1.7300000000000013
  episode_reward_mean: -3.1685999999999934
  episode_reward_min: -13.909999999999968
  episodes_this_iter: 4
  episodes_total: 3756
  experiment_id: 308d04df514f4288854eb163945dc05a
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 3.741178623682516e-47
          cur_lr: 5.000000000000001e-05
          entropy: 1.0357656598091125
          entropy_coeff: 0.009999999999999998
          kl: .inf
          policy_loss: 0.004608476327525245
          total_loss: 7328295533499.733
          vf_explained_var: -0.5432868003845215
          vf_loss: 3908244711378.489
    num_agent_steps_sampled: 1362000
    num_agent_steps_trained: 1362000
    num_steps_sampled: 1362000
    num_steps_trained: 1362000
  iterations_

Result for PPO_my_env_bff91_00000:
  agent_timesteps_total: 1363000
  custom_metrics: {}
  date: 2021-10-24_08-00-40
  done: false
  episode_len_mean: 225.27
  episode_media: {}
  episode_reward_max: -1.7300000000000013
  episode_reward_mean: -3.302999999999993
  episode_reward_min: -13.909999999999968
  episodes_this_iter: 4
  episodes_total: 3760
  experiment_id: 308d04df514f4288854eb163945dc05a
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 5.611767935523775e-47
          cur_lr: 5.000000000000001e-05
          entropy: 1.0106319983800252
          entropy_coeff: 0.009999999999999998
          kl: .inf
          policy_loss: 0.1787847739126947
          total_loss: 1347655783765.3333
          vf_explained_var: 0.10106462985277176
          vf_loss: 799030760425.2444
    num_agent_steps_sampled: 1363000
    num_agent_steps_trained: 1363000
    num_steps_sampled: 1363000
    num_steps_trained: 1363000
  iterations_si

Result for PPO_my_env_bff91_00000:
  agent_timesteps_total: 1364000
  custom_metrics: {}
  date: 2021-10-24_08-01-29
  done: false
  episode_len_mean: 223.62
  episode_media: {}
  episode_reward_max: -1.7300000000000013
  episode_reward_mean: -3.295899999999993
  episode_reward_min: -13.909999999999968
  episodes_this_iter: 5
  episodes_total: 3765
  experiment_id: 308d04df514f4288854eb163945dc05a
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 8.417651903285661e-47
          cur_lr: 5.000000000000001e-05
          entropy: 0.0
          entropy_coeff: 0.009999999999999998
          kl: 0.0
          policy_loss: -0.06497392306725185
          total_loss: 30290727424.0
          vf_explained_var: 0.14537595212459564
          vf_loss: 30290727424.0
    num_agent_steps_sampled: 1364000
    num_agent_steps_trained: 1364000
    num_steps_sampled: 1364000
    num_steps_trained: 1364000
  iterations_since_restore: 1364
  nod

2021-10-24 08:02:07,028	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
2021-10-24 08:02:07,028	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
Process _WandbLoggingProcess-1:
Traceback (most recent call last):
  File "/root/miniconda/envs/py37/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/integration/wandb.py", line 200, in run
    result = self.queue.get()
  File "/root/miniconda/envs/py37/lib/python3.7/multiprocessing/queues.py", line 94, in get
    res = self._recv_bytes()
  File "/root/miniconda/envs/py37/lib/python3.7/multiprocessing/connection.py", l

KeyboardInterrupt: 